In [1]:
import numpy as np
import pandas as pd
import matlab.engine
import yaml
import time
import importlib
import pathlib
import matplotlib.pyplot as plt
import csv
from tqdm import tqdm
from scipy.stats import pearsonr
from loguru import logger
from Entropy import ApproximateEntropy
from functools import partial, wraps
from itertools import product
import os
from typing import Union
from numbers import Number
from utilities import ZScore

In [2]:
import importlib
import Stationarity
importlib.reload(Stationarity)

<module 'Stationarity' from '/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Operations/Stationarity.py'>

In [3]:
def compare_outputs(outputs, exclude_keys=None):
    """
    Compare MATLAB and Python feature outputs, computing relative errors
    and Pearson correlations.

    Parameters
    ----------
    outputs : dict
        Nested dictionary of feature values with structure:
        {
            feature_name: {
                ts_id: {
                    'matlab': scalar_or_dict,
                    'python': scalar_or_dict
                }
            }
        }
    exclude_keys : set or list, optional
        Set or list of keys (feature names or feature.subkey) to exclude from comparison.

    Returns
    -------
    results : dict
        Dictionary mapping feature (or subfeature) names to correlation and stats:
        {
            'feature.subkey': {
                'r': float,
                'pval': float,
                'res_py': ndarray,
                'res_matlab': ndarray,
                'max_rel_err': float
            }
        }
    """
    if exclude_keys is None:
        exclude_keys = set()
    else:
        exclude_keys = set(exclude_keys)

    flat = {}
    for feat, ts_dict in outputs.items():
        for ts, run in ts_dict.items():
            ml = run['matlab']
            py = run['python']
            if isinstance(ml, dict) and isinstance(py, dict):
                for k, mlv in ml.items():
                    slot = f"{feat}.{k}"
                    if slot in exclude_keys or k not in py:
                        continue
                    pyv = py[k]
                    flat.setdefault(slot, {})[ts] = (mlv, pyv)
            elif isinstance(ml, Number) and isinstance(py, Number):
                if feat in exclude_keys:
                    continue
                flat.setdefault(feat, {})[ts] = (ml, py)
            else:
                raise ValueError(f"Feature {feat}@{ts} is neither both scalars nor both dicts.")

    results = {}
    for slot, tsmap in flat.items():
        ml_vals, py_vals = [], []
        rel_errors = []

        for ts, (mlv, pyv) in tsmap.items():
            ml_vals.append(mlv)
            py_vals.append(pyv)

            both_finite = np.isfinite(mlv) and np.isfinite(pyv)
            both_nan = np.isnan(mlv) and np.isnan(pyv)
            both_posinf = (mlv == np.inf) and (pyv == np.inf)
            both_neginf = (mlv == -np.inf) and (pyv == -np.inf)

            if both_finite:
                if mlv == 0:
                    rel_err = np.nan
                else:
                    rel_err = abs(mlv - pyv) / abs(mlv) * 100
                    rel_errors.append(rel_err)
                print(f"[{slot} | ts={ts}]  RelErr% = {rel_err:.2f}")
            elif both_nan or both_posinf or both_neginf:
                print(f"[{slot} | ts={ts}]  RelErr% = MATCH (both non-finite)")
            else:
                print(f"[{slot} | ts={ts}]  RelErr% = NaN (mismatch in finiteness)")

        ml_arr = np.array(ml_vals, dtype=float)
        py_arr = np.array(py_vals, dtype=float)
        finite_mask = np.isfinite(ml_arr) & np.isfinite(py_arr)

        if finite_mask.sum() > 1 and ml_arr[finite_mask].std() and py_arr[finite_mask].std():
            r, p = pearsonr(ml_arr[finite_mask], py_arr[finite_mask])
        else:
            r, p = np.nan, np.nan

        max_rel_err = np.nanmax(rel_errors) if rel_errors else np.nan

        results[slot] = {
            'r': r,
            'pval': p,
            'res_py': py_arr,
            'res_matlab': ml_arr,
            'max_rel_err': max_rel_err
        }

    return results

In [4]:
empirical1000 = []
with open("../../../empirical1000/hctsa_timeseries-data.csv") as csvfile:
    reader = csv.reader(csvfile, delimiter=',')
    for row in reader:
        # Convert each element from string to float (or int if appropriate)
        try:
            time_series = [float(value) for value in row if value != '']
            empirical1000.append(time_series)
        except ValueError as e:
            print(f"Skipping row due to conversion error: {row}")
            continue

In [5]:
def load_yaml(file):
    print(f"Loading configuration file: {file.split('/')[-1]}")
    funcs = {}
    with open(file) as f:
        yf = yaml.load(f, Loader=yaml.FullLoader)

    for module_name in yf:
        print(f"\n*** Importing module {module_name} *** \n")
        module = importlib.import_module(module_name)
        for function_name in yf[module_name]:
            # Get the function's configuration dictionary
            function_config = yf[module_name][function_name]
            # If no configs section exists or if it's empty, use a list with single empty dict
            if ('configs' not in function_config or function_config.get('configs') is None or 
                function_config.get('configs') == []):
                configs = [{}]
            else:
                configs = function_config.get('configs', [{}])

            for params in configs:
                # Handle the case where params is None
                if params is None:
                    params = {}
                    
                zscore_first = params.pop("zscore", False)
                param_keys, param_vals = zip(*params.items()) if params else ([], [])
                
                param_combinations = [dict(zip(param_keys, values)) 
                                   for values in product(*[v if isinstance(v, list) 
                                                        else [v] for v in param_vals])]
                
                # If no parameter combinations were generated, add empty dict
                if not param_combinations:
                    param_combinations = [{}]
                
                # create a function for each parameter combination
                for param_set in param_combinations:
                    feature_name = (f"{module_name}_{function_name}_" + 
                                  "_".join(f"{v}" for k, v in param_set.items())
                                  if param_set else f"{module_name}_{function_name}")
                    if not zscore_first:
                        feature_name += "_raw"
                    
                    print(f"Adding operation {feature_name} with params {param_set} "
                          f"(Z-score={zscore_first})")
                    
                    base_func = partial(getattr(module, function_name), **param_set)
                    if zscore_first:
                        base_func = zscore_decorator(base_func)
                    
                    # return the MATLAB callable corresponding to the python implementation for direct comparison
                    # make sure to check whethe the data needs to be zscored when calling the MATLAB func, cannot be wrapped as it is not a python function
                    # so needs to be done manually when calling the function.
                    hctsa_name = function_config.get('hctsa_name')
                    hctsa_callable = eval(f"eng.{hctsa_name}")

                    # keep ordered args only for testing YAML otherwise bloats
                    funcs[feature_name] = {'callable': base_func, 'params': param_set, 'hctsa_name': function_config.get('hctsa_name'), 
                                           'matlab_callable': hctsa_callable, 'isZscore': zscore_first, 'ordered_args': function_config.get('ordered_args')}
                    
    return funcs

In [6]:
def eval_comparison(yaml, data):
    func_dict = load_yaml(yaml)
    func_res = dict()
    for func in func_dict:
        print(f"Evalutating {func}")
        f = func_dict[func]
        python_func = f['callable']
        matlab_func = f['matlab_callable']
        hctsa_name = f['hctsa_name']
        isZscore = f['isZscore']
        params = f['params']
        ordered_args = []
        if params:
            order = f['ordered_args']
            ordered_args = [params[k] for k in order]
            
        print(f"Comparing to {hctsa_name}")
        res = dict()
        for i in range(len(data)):
            x = np.array(data[i])
            matlab_eval = matlab_func(ZScore(matlab.double(x)), ordered_args[0], matlab.double(ordered_args[1])) if isZscore else matlab_func(matlab.double(x), ordered_args[0], matlab.double(ordered_args[1]))
            python_eval = python_func(x)
            res[i] = {'matlab': matlab_eval, 'python': python_eval}
        func_res[func] = res
    return func_res

In [7]:
eng = matlab.engine.start_matlab()

In [8]:
proj_root = pathlib.Path("/Users/jmoo2880/Documents/hctsa")
eng.addpath(eng.genpath(str(proj_root)), nargout=0)
jar_path = "/Users/jmoo2880/Documents/hctsa/Toolboxes/infodynamics-dist/infodynamics.jar"
eng.eval(f"javaaddpath('{jar_path}')", nargout=0)
def zscore_decorator(func):
    @wraps(func)
    def wrapper(y, *args, **kwargs):
        y = ZScore(y)
        return func(y, *args, **kwargs)
    return wrapper

def range_constructor(loader, node):
    start, end = loader.construct_sequence(node)
    return list(range(start, end+1))
yaml.add_constructor("!range", range_constructor)

In [9]:
importlib.reload(Stationarity)
from Stationarity import LocalExtrema

In [73]:
funcs = load_yaml("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml")

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_LocalExtrema_l_50 with params {'howToWindow': 'l', 'n': 50} (Z-score=True)
Adding operation Stationarity_LocalExtrema_l_100 with params {'howToWindow': 'l', 'n': 100} (Z-score=True)
Adding operation Stationarity_LocalExtrema_n_25 with params {'howToWindow': 'n', 'n': 25} (Z-score=True)
Adding operation Stationarity_LocalExtrema_n_50 with params {'howToWindow': 'n', 'n': 50} (Z-score=True)
Adding operation Stationarity_LocalExtrema_n_100 with params {'howToWindow': 'n', 'n': 100} (Z-score=True)


In [74]:
localExtrema_evals = eval_comparison("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml", empirical1000)

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_LocalExtrema_l_50 with params {'howToWindow': 'l', 'n': 50} (Z-score=True)
Adding operation Stationarity_LocalExtrema_l_100 with params {'howToWindow': 'l', 'n': 100} (Z-score=True)
Adding operation Stationarity_LocalExtrema_n_25 with params {'howToWindow': 'n', 'n': 25} (Z-score=True)
Adding operation Stationarity_LocalExtrema_n_50 with params {'howToWindow': 'n', 'n': 50} (Z-score=True)
Adding operation Stationarity_LocalExtrema_n_100 with params {'howToWindow': 'n', 'n': 100} (Z-score=True)
Evalutating Stationarity_LocalExtrema_l_50
Comparing to ST_LocalExtrema
200
200
200
20
20
20
100
100
100
20
100
100
200
100
20
20
100
20
200
100
100
20
200
200
200
200
200
200
200
20
20
20
20
20
20
20
100
100
100
100
100
20
100
100
100
100
200
200
20
200
20
200
200
200
20
100
150
150
20
20
20
20
100
100
10
10
10
10
150
150
100
100
200
200
100
20
200
100
200
200
20
100
100
100
20
10

In [ ]:
[Stationarity_LocalExtrema_n_25.stdext | ts=288]  RelErr% = 100.00

In [76]:
res = compare_outputs(localExtrema_evals)

[Stationarity_LocalExtrema_l_50.meanrat | ts=0]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=1]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=2]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=3]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=4]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=5]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=6]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=7]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=8]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=9]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=10]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=11]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=12]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=13]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.meanrat | ts=14]  RelErr% = 0.00
[Stationarity_LocalExtrema_l_50.mea

In [77]:
[res[p]['r'] for p in res]

[np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(0.9999999999999999),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999999),
 np.float64(0.9999999999999999),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(0.9999999999999999),
 np.float64(0.9999999999999999),
 np.float64(0.9999999999999996),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999999),
 np.float64(0.9999999999999998),
 np.float64(0.9999999999999999),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(1.0),
 np.float64(0.9999999999999999),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(0.9999999999999997),
 np.float64(1.0),
 np.

In [68]:
res['Stationarity_LocalExtrema_n_25.diffmaxabsmin']['res_py'][757]

np.float64(0.3285778951082613)

In [69]:
res['Stationarity_LocalExtrema_n_25.diffmaxabsmin']['res_matlab'][757]

np.float64(0.32857789510826135)

In [54]:
[res[p]['r'] for p in res]

[np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(0.9999999999999999),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999999),
 np.float64(0.9999999999999999),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(0.9999999999999999),
 np.float64(0.9999999999999999),
 np.float64(0.9967143375150199),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999999),
 np.float64(0.9999999999999998),
 np.float64(0.9999999999999999),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(0.988914073021334),
 np.float64(0.9999999999999999),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(0.9999999999999997),
 np.floa

In [31]:
res['Stationarity_LocalExtrema_l_50.meanrat']['res_py'][435]

np.float64(20.390931029419608)

In [32]:
res['Stationarity_LocalExtrema_l_50.meanrat']['res_matlab'][435]

np.float64(5.576717270525093)

In [81]:
funcs2 = load_yaml("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml")

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_SimpleStats_zcross with params {'whatStat': 'zcross'} (Z-score=True)
Adding operation Stationarity_SimpleStats_pmcross with params {'whatStat': 'pmcross'} (Z-score=True)


In [82]:
def eval_comparison_ss(yaml, data):
    func_dict = load_yaml(yaml)
    func_res = dict()
    for func in func_dict:
        print(f"Evalutating {func}")
        f = func_dict[func]
        python_func = f['callable']
        matlab_func = f['matlab_callable']
        hctsa_name = f['hctsa_name']
        isZscore = f['isZscore']
        params = f['params']
        ordered_args = []
        if params:
            order = f['ordered_args']
            ordered_args = [params[k] for k in order]
            
        print(f"Comparing to {hctsa_name}")
        res = dict()
        for i in range(len(data)):
            x = np.array(data[i])
            matlab_eval = matlab_func(ZScore(matlab.double(x)), *ordered_args) if isZscore else matlab_func(matlab.double(x), *ordered_args)
            python_eval = python_func(x)
            res[i] = {'matlab': matlab_eval, 'python': python_eval}
        func_res[func] = res
    return func_res

In [85]:
ss_evals = eval_comparison_ss("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml", empirical1000)

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_SimpleStats_zcross with params {'whatStat': 'zcross'} (Z-score=True)
Adding operation Stationarity_SimpleStats_pmcross with params {'whatStat': 'pmcross'} (Z-score=True)
Evalutating Stationarity_SimpleStats_zcross
Comparing to ST_SimpleStats
Evalutating Stationarity_SimpleStats_pmcross
Comparing to ST_SimpleStats


In [87]:
res_ss = compare_outputs(ss_evals)

[Stationarity_SimpleStats_zcross | ts=0]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=1]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=2]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=3]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=4]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=5]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=6]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=7]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=8]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=9]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=10]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=11]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=12]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=13]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=14]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=15]  RelErr% = 0.00
[Stationarity_SimpleStats_zcross | ts=16]  RelErr% = 0.00
[Stationarity_SimpleStat

In [88]:
[res_ss[p]['r'] for p in res_ss]

[np.float64(0.9999999999999998), np.float64(1.0)]

In [90]:
funcs3 = load_yaml("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml")

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_MomentCorr_0.02_0.2_mean_std_none with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'std', 'whatTransform': 'none'} (Z-score=True)
Adding operation Stationarity_MomentCorr_0.02_0.2_mean_std_abs with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'std', 'whatTransform': 'abs'} (Z-score=True)
Adding operation Stationarity_MomentCorr_0.02_0.2_mean_std_sqrt with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'std', 'whatTransform': 'sqrt'} (Z-score=True)
Adding operation Stationarity_MomentCorr_0.02_0.2_mean_iqr_none with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'iqr', 'whatTransform': 'none'} (Z-score=True)
Adding operation Stationarity_MomentCorr_0.02_0.2_mean_iqr_abs with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'iqr', 'whatTransform': 'abs

In [102]:
def eval_comparison_mc(yaml, data):
    func_dict = load_yaml(yaml)
    func_res = dict()
    for func in func_dict:
        print(f"Evalutating {func}")
        f = func_dict[func]
        python_func = f['callable']
        matlab_func = f['matlab_callable']
        hctsa_name = f['hctsa_name']
        isZscore = f['isZscore']
        params = f['params']
        ordered_args = []
        if params:
            order = f['ordered_args']
            ordered_args = [params[k] for k in order]
            
        print(f"Comparing to {hctsa_name}")
        res = dict()
        for i in range(len(data)):
            print(i)
            x = np.array(data[i])
            matlab_eval = matlab_func(ZScore(matlab.double(x)), matlab.double(ordered_args[0]), matlab.double(ordered_args[1]), 
                                     ordered_args[2], ordered_args[3], ordered_args[4]) if isZscore else matlab_func(matlab.double(x), matlab.double(ordered_args[0]), matlab.double(ordered_args[1]), 
                                     ordered_args[2], ordered_args[3], ordered_args[4])
            python_eval = python_func(x)
            res[i] = {'matlab': matlab_eval, 'python': python_eval}
            res[i] = {'python': python_eval}
        func_res[func] = res
    return func_res

In [103]:
momcorr_evals = eval_comparison_mc("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml", empirical1000)

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_MomentCorr_0.02_0.2_mean_std_none with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'std', 'whatTransform': 'none'} (Z-score=True)
Adding operation Stationarity_MomentCorr_0.02_0.2_mean_std_abs with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'std', 'whatTransform': 'abs'} (Z-score=True)
Adding operation Stationarity_MomentCorr_0.02_0.2_mean_std_sqrt with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'std', 'whatTransform': 'sqrt'} (Z-score=True)
Adding operation Stationarity_MomentCorr_0.02_0.2_mean_iqr_none with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'iqr', 'whatTransform': 'none'} (Z-score=True)
Adding operation Stationarity_MomentCorr_0.02_0.2_mean_iqr_abs with params {'windowLength': 0.02, 'wOverlap': 0.2, 'mom1': 'mean', 'mom2': 'iqr', 'whatTransform': 'abs

Error using IN_MutualInfo (line 72)
Java exception occurred: 
infodynamics.utils.NonPositiveDefiniteMatrixException: CholeskyDecomposition is only performed on positive-definite matrices. Some reasons for non-positive-definite matrix are listed at http://www2.gsu.edu/~mkteer/npdmatri.html - note: a correlation matrix is non-positive-definite if you have more variables than observations
	at infodynamics.utils.MatrixUtils.CholeskyDecomposition(Unknown Source)
	at infodynamics.measures.continuous.gaussian.MutualInfoCalculatorMultiVariateGaussian.setCovariance(Unknown Source)
	at infodynamics.measures.continuous.gaussian.MutualInfoCalculatorMultiVariateGaussian.finaliseAddObservations(Unknown Source)
	at infodynamics.measures.continuous.MutualInfoMultiVariateCommon.setObservations(Unknown Source)

Error in ST_MomentCorr (line 133)
out.mi = IN_MutualInfo(M1,M2,'gaussian');
         ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^



MatlabExecutionError: 
  File /Users/jmoo2880/Documents/hctsa/Operations/IN_MutualInfo.m, line 72, in IN_MutualInfo

  File /Users/jmoo2880/Documents/hctsa/Operations/ST_MomentCorr.m, line 133, in ST_MomentCorr
Java exception occurred: 
infodynamics.utils.NonPositiveDefiniteMatrixException: CholeskyDecomposition is only performed on positive-definite matrices. Some reasons for non-positive-definite matrix are listed at http://www2.gsu.edu/~mkteer/npdmatri.html - note: a correlation matrix is non-positive-definite if you have more variables than observations
	at infodynamics.utils.MatrixUtils.CholeskyDecomposition(Unknown Source)
	at infodynamics.measures.continuous.gaussian.MutualInfoCalculatorMultiVariateGaussian.setCovariance(Unknown Source)
	at infodynamics.measures.continuous.gaussian.MutualInfoCalculatorMultiVariateGaussian.finaliseAddObservations(Unknown Source)
	at infodynamics.measures.continuous.MutualInfoMultiVariateCommon.setObservations(Unknown Source)


In [114]:
importlib.reload(Stationarity)
from Stationarity import MomentCorr

In [106]:
MomentCorr(ZScore(empirical1000[181]), 0.02, 0.2, 'mean', 'std', 'none')

[ 5.34880213e-02  1.85037171e-17  0.00000000e+00  0.00000000e+00
 -1.85037171e-17  0.00000000e+00  0.00000000e+00  1.85037171e-17
  0.00000000e+00  0.00000000e+00 -1.85037171e-17  0.00000000e+00
  0.00000000e+00  1.85037171e-17  0.00000000e+00  0.00000000e+00
 -1.85037171e-17  0.00000000e+00  0.00000000e+00  1.85037171e-17
  0.00000000e+00  0.00000000e+00 -1.85037171e-17  0.00000000e+00
  0.00000000e+00  1.85037171e-17  0.00000000e+00  0.00000000e+00
 -1.85037171e-17  0.00000000e+00  0.00000000e+00  1.85037171e-17
  0.00000000e+00  0.00000000e+00 -1.85037171e-17  0.00000000e+00
  0.00000000e+00  1.85037171e-17  0.00000000e+00  0.00000000e+00
 -1.85037171e-17  0.00000000e+00  0.00000000e+00  1.85037171e-17
  0.00000000e+00  0.00000000e+00 -1.85037171e-17  0.00000000e+00
  0.00000000e+00  1.85037171e-17  0.00000000e+00  0.00000000e+00
 -1.85037171e-17  0.00000000e+00  0.00000000e+00  1.85037171e-17
  0.00000000e+00  0.00000000e+00 -1.85037171e-17  0.00000000e+00]


{'R': np.float64(-1.0),
 'absR': np.float64(1.0),
 'density': np.float64(1.968930200649737e-06),
 'mi': inf}

In [108]:
funcs4 = load_yaml("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml")

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_TSLength_raw with params {} (Z-score=False)


In [110]:
def eval_comparison_l(yaml, data):
    func_dict = load_yaml(yaml)
    func_res = dict()
    for func in func_dict:
        print(f"Evalutating {func}")
        f = func_dict[func]
        python_func = f['callable']
        matlab_func = f['matlab_callable']
        hctsa_name = f['hctsa_name']
        isZscore = f['isZscore']
        params = f['params']
        ordered_args = []
        if params:
            order = f['ordered_args']
            ordered_args = [params[k] for k in order]
            
        print(f"Comparing to {hctsa_name}")
        res = dict()
        for i in range(len(data)):
            x = np.array(data[i])
            matlab_eval = matlab_func(ZScore(matlab.double(x)), *ordered_args) if isZscore else matlab_func(matlab.double(x), *ordered_args)
            python_eval = python_func(x)
            res[i] = {'matlab': matlab_eval, 'python': python_eval}
        func_res[func] = res
    return func_res

In [111]:
len_evals = eval_comparison_l("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml", empirical1000)

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_TSLength_raw with params {} (Z-score=False)
Evalutating Stationarity_TSLength_raw
Comparing to ST_Length


In [113]:
compare_outputs(len_evals)

[Stationarity_TSLength_raw | ts=0]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=1]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=2]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=3]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=4]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=5]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=6]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=7]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=8]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=9]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=10]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=11]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=12]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=13]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=14]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=15]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=16]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=17]  RelErr% = 0.00
[Stationarity_TSLength_raw | ts=18]  RelErr% = 0.00
[Stationarity_TSLength

{'Stationarity_TSLength_raw': {'r': np.float64(1.0),
  'pval': np.float64(0.0),
  'res_py': array([10000., 10000., 10000.,  1000.,  1000.,  1000.,  5000.,  5000.,
          5000.,  1000.,  5000.,  5000., 10000.,  5000.,  1000.,  1000.,
          5000.,  1000., 10000.,  5000.,  5000.,  1000., 10000., 10000.,
         10000., 10000., 10000., 10000., 10000.,  1000.,  1000.,  1000.,
          1000.,  1000.,  1000.,  1000.,  5000.,  5000.,  5000.,  5000.,
          5000.,  1000.,  5000.,  5000.,  5000.,  5000., 10000., 10000.,
          1000., 10000.,  1000., 10000., 10000., 10000.,  1000.,  5000.,
          7500.,  7500.,  1000.,  1000.,  1000.,  1000.,  5000.,  5000.,
           500.,   500.,   500.,   500.,  7500.,  7500.,  5000.,  5000.,
         10000., 10000.,  5000.,  1000., 10000.,  5000., 10000., 10000.,
          1000.,  5000.,  5000.,  5000.,  1000.,  5000., 10000.,  5000.,
         10000., 10000.,  1000.,  1000.,  5000.,  5000., 10000.,  1000.,
         10000.,  1000.,  1000., 1

In [13]:
funcs5 = load_yaml("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml")

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_FitPolynomial_1 with params {'k': 1} (Z-score=True)
Adding operation Stationarity_FitPolynomial_2 with params {'k': 2} (Z-score=True)
Adding operation Stationarity_FitPolynomial_3 with params {'k': 3} (Z-score=True)
Adding operation Stationarity_FitPolynomial_4 with params {'k': 4} (Z-score=True)


In [22]:
funcs5['Stationarity_FitPolynomial_1']['matlab_callable'](ZScore(empirical1000[1]))

matlab.double([[0.6712873432663917,0.1380771233168873,0.7753719977940098,0.006463692018080087,0.10478850348598163,1.8860774656972374,2.746787951885792,0.17234523627086934,0.5338331505464189,0.3741035341747891,0.09451889466105004,0.028166189737072096,0.9627623937518612,0.632360768705198,0.0018133169816092352,4.622704230745576e-05,0.05728665396691057,0.09563883398800366,0.013389368979389003,0.0004345868031666625,1.3764813790844312,0.02951039654234802,0.21815596231074583,0.09782937519263146,0.8849796983903924,2.7530693650530784,1.428879182096414,1.5863827313760441,0.5099362557242144,0.7614691946359743,1.3443427973157291,0.9053468127830921,0.4866092982411401,1.9772664878363453,0.10131161914366543,0.7349543848880258,0.046445444350972566,1.5684300978483283,0.11118700474851546,0.07737813130912158,0.8626035687034873,3.150821463627679,0.597655073481279,2.51627549399907,0.33954943130299314,0.1668913107278719,0.9327525305788112,0.2758256291942665,0.0022503033991999643,0.16541729415118053,0.127777

In [27]:
def eval_comparison_poly(yaml, data):
    func_dict = load_yaml(yaml)
    func_res = dict()
    for func in func_dict:
        print(f"Evalutating {func}")
        f = func_dict[func]
        python_func = f['callable']
        matlab_func = f['matlab_callable']
        hctsa_name = f['hctsa_name']
        isZscore = f['isZscore']
        params = f['params']
        ordered_args = []
        if params:
            order = f['ordered_args']
            ordered_args = [params[k] for k in order]
            
        print(f"Comparing to {hctsa_name}")
        res = dict()
        for i in range(len(data)):
            x = np.array(data[i])
            #print(ordered_args)
            matlab_eval = matlab_func(ZScore(matlab.double(x)).T, ordered_args[0]) if isZscore else matlab_func(matlab.double(x).T, ordered_args[0])
            python_eval = python_func(x)
            res[i] = {'matlab': matlab_eval, 'python': python_eval}
        func_res[func] = res
    return func_res

In [28]:
poly_eval = eval_comparison_poly("/Users/jmoo2880/Documents/py-hctsa-project/pyhctsa/Configurations/stationarity.yaml", empirical1000)

Loading configuration file: stationarity.yaml

*** Importing module Stationarity *** 

Adding operation Stationarity_FitPolynomial_1 with params {'k': 1} (Z-score=True)
Adding operation Stationarity_FitPolynomial_2 with params {'k': 2} (Z-score=True)
Adding operation Stationarity_FitPolynomial_3 with params {'k': 3} (Z-score=True)
Adding operation Stationarity_FitPolynomial_4 with params {'k': 4} (Z-score=True)
Evalutating Stationarity_FitPolynomial_1
Comparing to ST_FitPolynomial
Evalutating Stationarity_FitPolynomial_2
Comparing to ST_FitPolynomial
Evalutating Stationarity_FitPolynomial_3
Comparing to ST_FitPolynomial
Evalutating Stationarity_FitPolynomial_4
Comparing to ST_FitPolynomial


In [31]:
poly_eval_res = compare_outputs(poly_eval)

[Stationarity_FitPolynomial_1 | ts=0]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=1]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=2]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=3]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=4]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=5]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=6]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=7]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=8]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=9]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=10]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=11]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=12]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=13]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=14]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=15]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=16]  RelErr% = 0.00
[Stationarity_FitPolynomial_1 | ts=17]  RelErr% = 0.00
[Stationarity_FitPol

In [32]:
[poly_eval_res[p]['r'] for p in poly_eval_res]

[np.float64(1.0),
 np.float64(1.0),
 np.float64(0.9999999999999998),
 np.float64(1.0)]